# **GANgealing Mixed Reality Playground** 

This is an official Colab notebook for running a pre-trained [GANgealing](https://www.wpeebles.com/gangealing) checkpoint on video. We can use this to do dense tracking or to create object lenses. For example, we'll be putting a cartoon face on a cat, a moustache on Elon Musk and reindeer horns on a puppy!

**You can also upload your own video to use with the demo!**

Make sure you've selected a GPU accelerator (Runtime > Change runtime type > Hardware accelerator > GPU).

# Setup

This can take around 6 minutes, but you only have to do it once. You can ignore any warnings from pip.

In [ ]:
#@title
# Download the GANgealing repo:
!git clone https://github.com/wpeebles/gangealing.git
import gangealing, os
os.chdir('gangealing')
os.environ['PYTHONPATH'] = '/env/python:/content/gangealing'
!pip install ninja ray plotly==4.14.3 torch==1.10.1 torchvision==0.11.2 imageio==2.4.1 --upgrade
from applications.mixed_reality import run_gangealing_on_video
from applications import load_stn

Cloning into 'gangealing'...
remote: Enumerating objects: 319, done.
remote: Counting objects: 100% (53/53), done.
remote: Compressing objects: 100% (35/35), done.
remote: Total 319 (delta 21), reused 36 (delta 18), pack-reused 266
Receiving objects: 100% (319/319), 182.62 MiB | 31.06 MiB/s, done.
Resolving deltas: 100% (109/109), done.
Checking out files: 100% (125/125), done.
     |████████████████████████████████| 108 kB 5.4 MB/s 
     |████████████████████████████████| 57.6 MB 1.3 MB/s 
     |████████████████████████████████| 13.2 MB 32.5 MB/s 
     |██████████████████████████████▎ | 834.1 MB 1.4 MB/s eta 0:00:36tcmalloc: large alloc 1147494400 bytes == 0x56527e892000 @  0x7f4b07094615 0x565245a513bc 0x565245b3218a 0x565245a541cd 0x565245b46b3d 0x565245ac8458 0x565245ac302f 0x565245a55aba 0x565245ac82c0 0x565245ac302f 0x565245a55aba 0x565245ac4cd4 0x565245b47986 0x565245ac4350 0x565245b47986 0x565245ac4350 0x565245b47986 0x565245ac4350 0x565245a55f19 0x565245a99a79 0x565245a54b32 0

# Select Model (and Video)

You can choose between many different pre-trained models for humans🧑🏼‍🔬, dogs🐶, cats🐱, etc. Select the one you want in the dropdown and then run the cell to download it.

We provide a few videos you can select from for the demo. If you want to upload your own video, select "Upload my own video" in the second dropdown (you'll upload it below).

It may take a few minutes to download everything.

In [ ]:
from utils.download import download_model, download_video
model = '🧑🏼‍🔬 human (celeba)'  #@param ['🧑🏼‍🔬 human (celeba)', '🐶 dog', '🐱 cat', '🐦 bird (cub)', '🚲 bicycle', '📺 tvmonitor']
video = '🧑🏼‍🔬 elon'  #@param ["🐱 cutecat", "🧑🏼‍🔬 elon", "🐶 snowpuppy", "Upload my own video"]
if video != 'Upload my own video':
    video = video.split(' ')[1]
video_download_mode = 'fast' #@param ['fast', 'high quality']
video_online_dir = 'video_1024' if video_download_mode == 'high quality' else 'video'
model = model.split(' ')
if len(model) == 2:
  model = model[1]
else:
  model = model[2][1:-1]
checkpoint = download_model(model, 'pretrained_stn_only')
if video != 'Upload my own video':
  video_path = download_video(video, video_online_dir)
  video_size = 1024 if video_download_mode == 'high quality' else 512

  0%|          | 0/172252378 [00:00<?, ?it/s]

  0%|          | 0/100663296 [00:00<?, ?it/s]

  0%|          | 0/8192 [00:00<?, ?it/s]

# (Optional) Upload Your Own Video

**NOTE: Skip this cell if you're using one of our provided videos!**

You can upload your own video here to use for the demo. Pretty much all video formats are supported (`.mp4`, `.mov`, `.avi`, etc.). 

**Start running this cell and then click the "Choose Files" button below. The cell won't stop running until you upload your video file (or cancel).**

`video_resolution` is the resolution in pixels that your video will be resized to upon uploading. You can choose any value in the dropdown.


In [ ]:
from google.colab import files
from pathlib import Path
uploaded = files.upload()
# Convert the video to a folder of frames and then create an LMDB:
video_resolution = "512" #@param [128, 256, 512, 1024, 2048, 4096, 8192]
pad_mode = 'resize_small_side' #@param ["resize_small_side", "center", "border"]
os.environ['VIDEO_SIZE'] = video_size = str(video_resolution)
os.environ['PAD'] = pad_mode
os.environ['RAW_VIDEO_PATH'] = list(uploaded.keys())[0]
video = Path(os.environ['RAW_VIDEO_PATH']).stem
os.environ['FRAME_PATH'] = f'data/video_frames/{video}'
os.environ['VIDEO_NAME'] = video
video_path = f'data/{video}'
!chmod 777 process_video.sh
!./process_video.sh "$RAW_VIDEO_PATH"
!python prepare_data.py --path "$FRAME_PATH" --out "data/$VIDEO_NAME" --pad "$PAD" --size "$VIDEO_SIZE"

Saving IMG_0268.mov to IMG_0268 (1).mov
ffmpeg version 3.4.8-0ubuntu0.2 Copyright (c) 2000-2020 the FFmpeg developers
  built with gcc 7 (Ubuntu 7.5.0-3ubuntu1~18.04)
  configuration: --prefix=/usr --extra-version=0ubuntu0.2 --toolchain=hardened --libdir=/usr/lib/x86_64-linux-gnu --incdir=/usr/include/x86_64-linux-gnu --enable-gpl --disable-stripping --enable-avresample --enable-avisynth --enable-gnutls --enable-ladspa --enable-libass --enable-libbluray --enable-libbs2b --enable-libcaca --enable-libcdio --enable-libflite --enable-libfontconfig --enable-libfreetype --enable-libfribidi --enable-libgme --enable-libgsm --enable-libmp3lame --enable-libmysofa --enable-libopenjpeg --enable-libopenmpt --enable-libopus --enable-libpulse --enable-librubberband --enable-librsvg --enable-libshine --enable-libsnappy --enable-libsoxr --enable-libspeex --enable-libssh --enable-libtheora --enable-libtwolame --enable-libvorbis --enable-libvpx --enable-libwavpack --enable-libwebp --enable-libx265 --enab

# Choose Object Lense

Run the cell and then select the object you want to propagate in the dropdown menu. You can also select "dense tracking." You can change your selection at any time.

In [ ]:
#@title
import ipywidgets as widgets
from glob import glob
options = [os.path.basename(f) for f in glob(f'assets/objects/{model}/*.png')]
options.append('dense tracking')
object_picker = widgets.Dropdown(options=options)
object_picker

Dropdown(options=('celeba_pokemon.png', 'celeba_moustache.png', 'dense tracking'), value='celeba_pokemon.png')

# Run Mixed Reality

Run the cell to generate and display the output Mixed Reality video! 

Depending on the length of your video and quality of GPU, **it should take a couple of minutes to run this cell.** You can monitor progress below.

If you get an out of memory error, you can check the `memory_efficient_but_slower` box.

**Tip**: If you want to download the output video, we recommend downloading it from the Colab file system. We have to slightly compress the output video to display it in Colab, so the video saved directly to the file system will be higher-quality than the one displayed below.

In [ ]:
fps = 30 #@param {type:"integer"}
blend_alg = 'alpha'  #@param ["alpha", "laplacian", "laplacian_light"]
batch_size =  1#@param {type:"integer"}
use_flipping = False #@param {type:"boolean"}
memory_efficient_but_slower = False #@param {type:"boolean"}

# The cutecat video is 60 FPS (elon and snowpuppy are 30 FPS):
if 'cutecat' in video_path:
  fps = 60

class MyDict(): 
  def __init__(self): pass

# Assign a bunch of arguments. For some reason, this demo
# runs way faster when invoking python commands directly 
# than calling python from bash.
args = MyDict()
args.real_size = int(video_size)
args.real_data_path = video_path
args.fps = fps
args.batch = batch_size
args.blend_alg = blend_alg
args.transform = ['similarity', 'flow']
args.flow_size = 128
args.stn_channel_multiplier = 0.5
args.num_heads = 1
args.distributed = False  # Colab only uses 1 GPU
args.clustering = False
args.cluster = None
args.objects = True
args.no_flip_inference = not use_flipping
args.save_frames = memory_efficient_but_slower
args.overlay_congealed = False
args.ckpt = model
args.override = False
args.save_correspondences = False
args.out = 'visuals'
if object_picker.value == 'dense tracking':
  args.label_path = f'assets/masks/{model}_mask.png'
  # Feel free to change the parameters below:
  args.resolution = 128
  args.sigma = 1.3
  args.opacity = 0.8
  args.objects = False
else:  # object lense
  args.label_path = f'assets/objects/{model}/{object_picker.value}'
  args.resolution = 4 * int(video_size)
  args.sigma = 0.3
  args.opacity = 1.0
  args.objects = True

# Run Mixed Reality!
stn = load_stn(args)
print('Running Spatial Transformer on frames...')
run_gangealing_on_video(args, stn, classifier=None)

print('Preparing videos to be displayed...')
# Display the output video: (snippet from https://stackoverflow.com/a/65273831)
from IPython.display import HTML
from base64 import b64encode
num = len(list(glob(f'{video}_compressed*')))
compressed_name = f'{video}_compressed{num}.mp4'
congealed_compressed_name = f'{video}_compressed_congealed{num}.mp4'
path = f'visuals/video_{video}/propagated.mp4'
congealed_path = f'visuals/video_{video}/congealed.mp4'
os.system(f"ffmpeg -i {path} -vcodec libx264 {compressed_name}")
os.system(f"ffmpeg -i {congealed_path} -vcodec libx264 {congealed_compressed_name}")
mp4 = open(compressed_name,'rb').read()
mp4_congealed = open(congealed_compressed_name, 'rb').read()
data_url = "data:video/mp4;base64," + b64encode(mp4).decode()
congealed_data_url = "data:video/mp4;base64," + b64encode(mp4_congealed).decode()
print(f'HIGHEST QUALITY output videos can be found at /content/gangealing/visuals/{video}')
HTML("""<video width=512 autoplay controls loop><source src="%s" type="video/mp4"></video> <video width=512 autoplay controls loop><source src="%s" type="video/mp4"></video>""" % (data_url, congealed_data_url))

Running Spatial Transformer on frames...


100%|██████████| 445/445 [06:10<00:00,  1.20it/s]

[MoviePy] >>>> Building video visuals/video_elon/propagated.mp4
[MoviePy] Writing video visuals/video_elon/propagated.mp4



100%|█████████▉| 445/446 [01:21<00:00,  5.46it/s]


[MoviePy] Done.
[MoviePy] >>>> Video ready: visuals/video_elon/propagated.mp4 

[MoviePy] >>>> Building video visuals/video_elon/congealed.mp4
[MoviePy] Writing video visuals/video_elon/congealed.mp4


100%|█████████▉| 445/446 [01:36<00:00,  4.62it/s]


[MoviePy] Done.
[MoviePy] >>>> Video ready: visuals/video_elon/congealed.mp4 

Done.
Preparing videos to be displayed...
HIGHEST QUALITY output videos can be found at /content/gangealing/visuals/elon


# Bonus: Creating Your Own Object Lenses

Want to propagate a custom object to a video with this notebook? You'll need to create a new RGBA image saved as a png. You can take the pre-computed average congealed image for your model of interest (located in `gangealing/assets/averages`) and load it into an image editor like Photoshop. Then, overlay your custom object on the template and export the object as an RGBA png image. Upload your new png to the `gangealing/assets/MODEL` folder (where `MODEL` is the model you want to use). Re-run the "Choose Object Lense" cell; you can then select it from the dropdown menu.

**Tip**: We recommend exporting the png at a high resolution (e.g., export at 4096x4096 resolution if you want to propagate to a 1024x1024 video).